In [ ]:
# File Settings
#ROOT_FOLDERS = ['/home/marrakchi/TFM/Datasets/SSSS/','/home/marrakchi/TFM/Datasets/120hSS/asr-spanish-v1-carlfm01/']
#CSV_FILE_PATH_1 = ROOT_FOLDERS[0] + 'transcript.txt'
#CSV_FILE_PATH_2 = ROOT_FOLDERS[1] + 'files.csv'
#CSV_FILE_PATH = [CSV_FILE_PATH_1, CSV_FILE_PATH_2]

#SAVE_RESULTS_PATH = '/TFM/TFM_env/resultados/'
#SAVE_MODELS_PATH = '/home/marrakchi/TFM/resultados/'
path_dataset ='/home/marrakchi/TFM/TFM_env/Datasets/ExKaldiASRDatasetFormat/' 


In [2]:
# Systems Libraries
import os
import time

# For audio processing
import librosa
import librosa.display
import IPython as ipd
from IPython.display import display, HTML # For displaying tables

#from torchsummary import summary

# For data processing
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# For Neural networks
import torch
from torch import nn
import pickle as pkl
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader


# For visualization
import matplotlib
import matplotlib.pyplot as plt
%matplotlib inline


# For text processing
import string

# Scripts created by me:
#import herramientas as utils
#import models
#import textprocessor
#import speechdataset

# Import Early Stop https://github.com/Bjarten/early-stopping-pytorch
#from pytorchtools import EarlyStopping

from datetime import datetime

# Import sox (for preprocessing data)
#import sox

# Import exkaldi package
import exkaldi
exkaldi.info.reset_kaldi_root('/kaldi')

exkaldi.info.reset_kaldi_root( yourPath )
If not, ERROR will occur when implementing some core functions.


In [3]:
# ExKaldi Configuration
ExKaldiInfo = exkaldi.info
print(ExKaldiInfo)
print(ExKaldiInfo.KALDI)
print(ExKaldiInfo.KALDI_ROOT)

ExKaldiInfo(version='1.3.5.4', major='1', minor='3', patch='5', upload='4')
Kaldi(version='5.5', major='5', minor='5')
/kaldi


In [4]:
# Ensuring that GPU are detected/available and ready to use
print(torch.cuda.device_count())
print(torch.cuda.is_available())

0
False


In [5]:
# CUDA_VISIBLE_DEVICES=1

# Data processing

In [11]:
"""# Preparing data for ExKaldi (WAV file)

from os import listdir
# Paths
path_batalla ='/home/marrakchi/TFM/Datasets/SSSS/batalla_arapiles/'
path_bailen ='/home/marrakchi/TFM/Datasets/SSSS/bailen/'
path_marzo ='/home/marrakchi/TFM/Datasets/SSSS/19demarzo/'
path_120 ='/home/marrakchi/TFM/Datasets/120hSS/asr-spanish-v1-carlfm01/audios/'
path_output ='/home/marrakchi/TFM/Datasets/ExKaldiASRDatasetFormat/wav/' 

# Getting all the audio paths
batalla_list = listdir(path_batalla)
bailen_list = listdir(path_bailen)
marzo_list = listdir(path_marzo)
SS120_list = listdir(path_120)

# Order the audio paths
batalla_list.sort()
bailen_list.sort()
marzo_list.sort()
SS120_list.sort()

# create transformer with the output format desired
tfm = sox.Transformer()
tfm.set_output_format(bits=16, encoding='signed-integer')

# Transform all the audios into the correct format
for i,path in enumerate(batalla_list):
    if i==0:
        print(i)
        print(path)
    # Create output file
    tfm.build_file(input_filepath=path_batalla+path, output_filepath=path_output+path)
    
# Transform all the audios into the correct format
for i,path in enumerate(bailen_list):
    if i==0:
        print(i)
        print(path)
    # Create output file
    tfm.build_file(input_filepath=path_bailen+path, output_filepath=path_output+path)    
    
# Transform all the audios into the correct format
for i,path in enumerate(marzo_list):
    if i==0:
        print(i)
        print(path)
    # Create output file
    tfm.build_file(input_filepath=path_marzo+path, output_filepath=path_output+path)
    
# Transform all the audios into the correct format
for i,path in enumerate(SS120_list):
    if i==0:
        print(i)
        print(path)
    # Create output file
    tfm.build_file(input_filepath=path_120+path, output_filepath=path_output+path)

print(len(batalla_list)) --> 4598
print(len(bailen_list)) --> 3240
print(len(marzo_list)) --> 3273
print(len(SS120_list)) --> 112845
wav_list = batalla_list+bailen_list+marzo_list+SS120_list 
print(len(wav_list)) --> 123956

## Create txt file with all the wav names
#mi_path = path_dataset+"wav_names.txt"
#with open(mi_path, "w") as opfile:
#    opfile.write("\n".join(wav_list))
#    opfile.close()
    
# Read txt file as a list
mi_path = path_dataset+"wav_names.txt"
file = open(mi_path, 'r') 
text = file.read() 
wav_list = text.split("\n")
file.close()

print(len(wav_list))

"""

In [83]:
# Read txt file as a list
mi_path = path_dataset+"wav_names.txt"
file = open(mi_path, 'r') 
text = file.read() 
wav_list = text.split("\n")
file.close()

print(len(wav_list))

123956


In [90]:
# Create utterance_to_speaker and speaker_to_utterance files

utt2spk = exkaldi.ListTable(name="utt2spk")
spk2utt = exkaldi.ListTable(name="spk2utt")

for name in wav_list:
    uttID = name[:-4]
    if ('batalla' in name) or ('bailen' in name) or ('19demarzo' in name):
        speaker = '0000' # narrator/story-teller
        #print(name+' --> '+speaker)
    else:
        speaker = name[0]
    # 2. utt2spk
    utt2spk[uttID] = speaker
    # 3. spk2utt
    if speaker not in spk2utt.keys():
        spk2utt[speaker] = f"{uttID}"
    else:
        spk2utt[speaker] += f" {uttID}"
# Save files
utt2spk.save( os.path.join(path_dataset, "utt2spk") )
spk2utt.save( os.path.join(path_dataset, "spk2utt") )  

19demarzo_0000.wav --> 0000
19demarzo_0001.wav --> 0000
19demarzo_0002.wav --> 0000
19demarzo_0003.wav --> 0000
19demarzo_0004.wav --> 0000
19demarzo_0005.wav --> 0000
19demarzo_0006.wav --> 0000
19demarzo_0007.wav --> 0000
19demarzo_0008.wav --> 0000
19demarzo_0009.wav --> 0000
19demarzo_0010.wav --> 0000
19demarzo_0011.wav --> 0000
19demarzo_0012.wav --> 0000
19demarzo_0013.wav --> 0000
19demarzo_0014.wav --> 0000
19demarzo_0015.wav --> 0000
19demarzo_0016.wav --> 0000
19demarzo_0017.wav --> 0000
19demarzo_0018.wav --> 0000
19demarzo_0019.wav --> 0000
19demarzo_0020.wav --> 0000
19demarzo_0021.wav --> 0000
19demarzo_0022.wav --> 0000
19demarzo_0023.wav --> 0000
19demarzo_0024.wav --> 0000
19demarzo_0025.wav --> 0000
19demarzo_0026.wav --> 0000
19demarzo_0027.wav --> 0000
19demarzo_0028.wav --> 0000
19demarzo_0029.wav --> 0000
19demarzo_0030.wav --> 0000
19demarzo_0031.wav --> 0000
19demarzo_0032.wav --> 0000
19demarzo_0033.wav --> 0000
19demarzo_0034.wav --> 0000
19demarzo_0035.wav -

19demarzo_2059.wav --> 0000
19demarzo_2060.wav --> 0000
19demarzo_2061.wav --> 0000
19demarzo_2062.wav --> 0000
19demarzo_2063.wav --> 0000
19demarzo_2064.wav --> 0000
19demarzo_2065.wav --> 0000
19demarzo_2066.wav --> 0000
19demarzo_2067.wav --> 0000
19demarzo_2068.wav --> 0000
19demarzo_2069.wav --> 0000
19demarzo_2070.wav --> 0000
19demarzo_2071.wav --> 0000
19demarzo_2072.wav --> 0000
19demarzo_2073.wav --> 0000
19demarzo_2074.wav --> 0000
19demarzo_2075.wav --> 0000
19demarzo_2076.wav --> 0000
19demarzo_2077.wav --> 0000
19demarzo_2078.wav --> 0000
19demarzo_2079.wav --> 0000
19demarzo_2080.wav --> 0000
19demarzo_2081.wav --> 0000
19demarzo_2082.wav --> 0000
19demarzo_2083.wav --> 0000
19demarzo_2084.wav --> 0000
19demarzo_2085.wav --> 0000
19demarzo_2086.wav --> 0000
19demarzo_2087.wav --> 0000
19demarzo_2088.wav --> 0000
19demarzo_2089.wav --> 0000
19demarzo_2090.wav --> 0000
19demarzo_2091.wav --> 0000
19demarzo_2092.wav --> 0000
19demarzo_2093.wav --> 0000
19demarzo_2094.wav -

bailen_0000.wav --> 0000
bailen_0001.wav --> 0000
bailen_0002.wav --> 0000
bailen_0003.wav --> 0000
bailen_0004.wav --> 0000
bailen_0005.wav --> 0000
bailen_0006.wav --> 0000
bailen_0007.wav --> 0000
bailen_0008.wav --> 0000
bailen_0009.wav --> 0000
bailen_0010.wav --> 0000
bailen_0011.wav --> 0000
bailen_0012.wav --> 0000
bailen_0013.wav --> 0000
bailen_0014.wav --> 0000
bailen_0015.wav --> 0000
bailen_0016.wav --> 0000
bailen_0017.wav --> 0000
bailen_0018.wav --> 0000
bailen_0019.wav --> 0000
bailen_0020.wav --> 0000
bailen_0021.wav --> 0000
bailen_0022.wav --> 0000
bailen_0023.wav --> 0000
bailen_0024.wav --> 0000
bailen_0025.wav --> 0000
bailen_0026.wav --> 0000
bailen_0027.wav --> 0000
bailen_0028.wav --> 0000
bailen_0029.wav --> 0000
bailen_0030.wav --> 0000
bailen_0031.wav --> 0000
bailen_0032.wav --> 0000
bailen_0033.wav --> 0000
bailen_0034.wav --> 0000
bailen_0035.wav --> 0000
bailen_0036.wav --> 0000
bailen_0037.wav --> 0000
bailen_0038.wav --> 0000
bailen_0039.wav --> 0000


bailen_2327.wav --> 0000
bailen_2328.wav --> 0000
bailen_2329.wav --> 0000
bailen_2330.wav --> 0000
bailen_2331.wav --> 0000
bailen_2332.wav --> 0000
bailen_2333.wav --> 0000
bailen_2334.wav --> 0000
bailen_2335.wav --> 0000
bailen_2336.wav --> 0000
bailen_2337.wav --> 0000
bailen_2338.wav --> 0000
bailen_2339.wav --> 0000
bailen_2340.wav --> 0000
bailen_2341.wav --> 0000
bailen_2342.wav --> 0000
bailen_2343.wav --> 0000
bailen_2344.wav --> 0000
bailen_2345.wav --> 0000
bailen_2346.wav --> 0000
bailen_2347.wav --> 0000
bailen_2348.wav --> 0000
bailen_2349.wav --> 0000
bailen_2350.wav --> 0000
bailen_2351.wav --> 0000
bailen_2352.wav --> 0000
bailen_2353.wav --> 0000
bailen_2354.wav --> 0000
bailen_2355.wav --> 0000
bailen_2356.wav --> 0000
bailen_2357.wav --> 0000
bailen_2358.wav --> 0000
bailen_2359.wav --> 0000
bailen_2360.wav --> 0000
bailen_2361.wav --> 0000
bailen_2362.wav --> 0000
bailen_2363.wav --> 0000
bailen_2364.wav --> 0000
bailen_2365.wav --> 0000
bailen_2366.wav --> 0000


batalla_arapiles_1343.wav --> 0000
batalla_arapiles_1344.wav --> 0000
batalla_arapiles_1345.wav --> 0000
batalla_arapiles_1346.wav --> 0000
batalla_arapiles_1347.wav --> 0000
batalla_arapiles_1348.wav --> 0000
batalla_arapiles_1349.wav --> 0000
batalla_arapiles_1350.wav --> 0000
batalla_arapiles_1351.wav --> 0000
batalla_arapiles_1352.wav --> 0000
batalla_arapiles_1353.wav --> 0000
batalla_arapiles_1354.wav --> 0000
batalla_arapiles_1355.wav --> 0000
batalla_arapiles_1356.wav --> 0000
batalla_arapiles_1357.wav --> 0000
batalla_arapiles_1358.wav --> 0000
batalla_arapiles_1359.wav --> 0000
batalla_arapiles_1360.wav --> 0000
batalla_arapiles_1361.wav --> 0000
batalla_arapiles_1362.wav --> 0000
batalla_arapiles_1363.wav --> 0000
batalla_arapiles_1364.wav --> 0000
batalla_arapiles_1365.wav --> 0000
batalla_arapiles_1366.wav --> 0000
batalla_arapiles_1367.wav --> 0000
batalla_arapiles_1368.wav --> 0000
batalla_arapiles_1369.wav --> 0000
batalla_arapiles_1370.wav --> 0000
batalla_arapiles_137

batalla_arapiles_3352.wav --> 0000
batalla_arapiles_3353.wav --> 0000
batalla_arapiles_3354.wav --> 0000
batalla_arapiles_3355.wav --> 0000
batalla_arapiles_3356.wav --> 0000
batalla_arapiles_3357.wav --> 0000
batalla_arapiles_3358.wav --> 0000
batalla_arapiles_3359.wav --> 0000
batalla_arapiles_3360.wav --> 0000
batalla_arapiles_3361.wav --> 0000
batalla_arapiles_3362.wav --> 0000
batalla_arapiles_3363.wav --> 0000
batalla_arapiles_3364.wav --> 0000
batalla_arapiles_3365.wav --> 0000
batalla_arapiles_3366.wav --> 0000
batalla_arapiles_3367.wav --> 0000
batalla_arapiles_3368.wav --> 0000
batalla_arapiles_3369.wav --> 0000
batalla_arapiles_3370.wav --> 0000
batalla_arapiles_3371.wav --> 0000
batalla_arapiles_3372.wav --> 0000
batalla_arapiles_3373.wav --> 0000
batalla_arapiles_3374.wav --> 0000
batalla_arapiles_3375.wav --> 0000
batalla_arapiles_3376.wav --> 0000
batalla_arapiles_3377.wav --> 0000
batalla_arapiles_3378.wav --> 0000
batalla_arapiles_3379.wav --> 0000
batalla_arapiles_338

'/home/marrakchi/TFM/TFM_env/Datasets/ExKaldiASRDatasetFormat/spk2utt'

In [98]:
for key, value in spk2utt.items() :
    print(key) # speakers? --> 17?

0
1
0000
2
3
4
5
6
7
8
9
a
b
c
d
e
f


In [6]:
# Generate utterance_to_speaker and speaker_to_utterance files for train/val/test

trainTrans = exkaldi.load_transcription(os.path.join(path_dataset,'data/train',"text"))
valTrans = exkaldi.load_transcription(os.path.join(path_dataset,'data/val',"text"))
testTrans = exkaldi.load_transcription(os.path.join(path_dataset,'data/test',"text"))

utt2spkTrain = exkaldi.ListTable(name="utt2spk")
spk2uttTrain = exkaldi.ListTable(name="spk2utt")
utt2spkTest = exkaldi.ListTable(name="utt2spk")
spk2uttTest = exkaldi.ListTable(name="spk2utt")
utt2spkVal = exkaldi.ListTable(name="utt2spk")
spk2uttVal = exkaldi.ListTable(name="spk2utt")

for name in trainTrans:
    uttID = name
    #print(uttID)
    if ('batalla' in name) or ('bailen' in name) or ('19demarzo' in name):
        speaker = '0000' # narrator/story-teller
        
    else:
        speaker = name[0]
        print(name+' --> '+speaker)
    # 2. utt2spk
    utt2spkTrain[uttID] = speaker
    # 3. spk2utt
    if speaker not in spk2uttTrain.keys():
        spk2uttTrain[speaker] = f"{uttID}"
    else:
        spk2uttTrain[speaker] += f" {uttID}"
    
# Save files
utt2spkTrain.save( os.path.join(path_dataset,'data/train', "utt2spk") )
spk2uttTrain.save( os.path.join(path_dataset,'data/train', "spk2utt") )

for name in valTrans:
    uttID = name
    if ('batalla' in name) or ('bailen' in name) or ('19demarzo' in name):
        speaker = '0000' # narrator/story-teller
        #print(name+' --> '+speaker)
    else:
        speaker = name[0]
    # 2. utt2spk
    utt2spkVal[uttID] = speaker
    # 3. spk2utt
    if speaker not in spk2uttVal.keys():
        spk2uttVal[speaker] = f"{uttID}"
    else:
        spk2uttVal[speaker] += f" {uttID}"
        
# Save files
utt2spkVal.save( os.path.join(path_dataset,'data/val', "utt2spk") )
spk2uttVal.save( os.path.join(path_dataset,'data/val', "spk2utt") )

for name in testTrans:
    uttID = name
    if ('batalla' in name) or ('bailen' in name) or ('19demarzo' in name):
        speaker = '0000' # narrator/story-teller
        #print(name+' --> '+speaker)
    else:
        speaker = name[0]
    # 2. utt2spk
    utt2spkTest[uttID] = speaker
    # 3. spk2utt
    if speaker not in spk2uttTest.keys():
        spk2uttTest[speaker] = f"{uttID}"
    else:
        spk2uttTest[speaker] += f" {uttID}"

# Save files
utt2spkTest.save( os.path.join(path_dataset,'data/test', "utt2spk") )
spk2uttTest.save( os.path.join(path_dataset,'data/test', "spk2utt") )

28a8b41c-e1ff-44bd-b569-aed552f6bd5c --> 2
c2e2be60-ef6d-458b-b300-2175bc108e9f --> c
2c6d6777-2ea2-4eb2-b5eb-14cac43213ac --> 2
621400a1-dd55-49d3-8ee6-9a753041c454 --> 6
bfd182ed-2dd9-4ea4-824b-4bea66f881b4 --> b
1c392d26-8f75-4ba4-8ab7-445075d2b501 --> 1
2d77fe0e-b599-4df0-afa4-3cc2e5a6228f --> 2
bd9d0499-cb3e-4523-80ef-be076d45f176 --> b
f9c146f0-2924-4224-a3d9-ec11c22b1ed6 --> f
6e2966fb-e496-4e8a-8c55-ff5cf6160c92 --> 6
94dd6b29-1a6f-4aa2-bc51-080d44cfbf0a --> 9
d9c7a53c-2e23-47e4-81e7-c0b4ffc29f79 --> d
da7da914-f2e9-4a69-9b82-6ddeec78cf4b --> d
978099f5-3fa8-41bb-a31c-792ff8b60586 --> 9
f73fe601-fa3a-40a5-8b0d-d346e82247eb --> f
87f0c4ef-eac5-440b-9621-ffae1e26dc76 --> 8
9c6edad5-17b8-4707-9646-6346330bea4a --> 9
f80f5108-c0a5-4a4d-b8d3-cecaaded74be --> f
a457ed59-7061-4f98-a548-0b1ad54a3d9e --> a
6765c9d7-94db-45d5-b464-d0052d5b788d --> 6
386755a8-8c7d-4324-a65c-c2381bdf882a --> 3
348fe75b-3b3c-4f6d-a799-f055583a0137 --> 3
54ebc071-7389-495e-bde8-a42533396f16 --> 5
6efc80d4-27

d530581e-6562-413d-9816-aac8f0659da1 --> d
a08f55a6-246e-43f5-a63b-1df2f316b0b8 --> a
cf4cf1ff-ae73-4020-8b88-7f50dbc7d045 --> c
f9035510-2670-4e52-b7f3-a8d2eb1f9882 --> f
bedebcef-cadf-47eb-bab9-b39eed131d51 --> b
1a514653-3646-48fc-8ada-5ac8ac1834bd --> 1
304498f2-0c4e-406d-a9e7-42e698285523 --> 3
ff80da05-cad3-441e-a26c-a38fc0c99073 --> f
b2960a31-2c0f-4c94-8414-30570a521048 --> b
940c1846-6724-41b4-89f1-49fab8f41232 --> 9
93314f9c-6ab6-41e0-a19d-1a9173fd04b1 --> 9
c615b9ec-b5cf-426e-a4af-bc9889267271 --> c
af1c456b-a67b-487d-8cde-6e3942c1ac2e --> a
01d76da7-358a-4d8b-8cf0-afac845dd08b --> 0
34b49123-2c2f-428d-bec2-630ddeca4667 --> 3
4aa8f7d0-8a29-4e65-b56c-ba1776fedb5d --> 4
9f67c5c3-6610-4a6e-9f0d-1962ddcc7675 --> 9
66108848-8bc0-46ee-891d-17cf809be6a8 --> 6
9c260af5-df8e-4fe6-862f-2d090a532459 --> 9
c66297aa-2b94-4077-93bd-2746cace1e0b --> c
8b53ab8d-5032-4551-b7a6-cc81c989b995 --> 8
79e83f52-add2-41a0-8c5a-806a1a070a80 --> 7
b809b340-6b18-4ede-b932-192abddf020d --> b
cad8d866-b1

22b3fa4f-5ca0-4f21-b2e8-812b8a53bdcd --> 2
d284e2e2-7ffb-485b-8489-e01dbcad4566 --> d
4babffff-c315-4558-a7bb-e2a80379df1e --> 4
aa1460b9-e1ce-450e-8c6c-ae80464b86d3 --> a
504540b6-20bd-4b26-b000-e10c60345bf7 --> 5
2a760027-b661-4ede-b2ce-cb683d629770 --> 2
d89c02c5-f337-41c1-bc27-0dac10c31514 --> d
9a9c118e-451f-4535-b327-ed9514d68306 --> 9
4c12d3e0-4b87-49c4-8789-33d017d74e0b --> 4
7d2dfbf2-6496-4e18-8700-424573d37ad4 --> 7
110446bc-b1d6-4e32-b8ee-019c3032691f --> 1
2b8872a8-b7b4-47b6-b9a6-30e73c957e14 --> 2
978dd810-aba9-4cea-8b02-59d51113f7d2 --> 9
f78007ac-dd22-48d8-a162-82cc309fd4ad --> f
1ffebbe5-7b25-4445-98e1-16da5aa9059c --> 1
787e8cdc-52d2-43ac-9a1a-de383715a753 --> 7
01d15c0b-c65e-4e63-8d52-cb40837f7a33 --> 0
af6446ef-b0c2-4134-9991-7675c9c068cf --> a
7404631b-ba33-44f4-aa59-393a8cb39a35 --> 7
726344d3-08c2-47db-853f-03148b7e096c --> 7
32f4f1d5-36e8-46f7-8cf9-fa004214a38d --> 3
c5b4f3a1-5af2-4e0e-a15c-aa32cf25f63e --> c
e44d7692-13c8-4ef0-9607-593b35517fa0 --> e
dc481012-26

23f7f963-d13e-401f-9530-935e0176dad4 --> 2
3636b19d-287d-4b9f-a788-6fe306aeb96d --> 3
21219c2d-6d81-4f8e-8230-cdc55d4bf1ea --> 2
7a6c5191-f822-4b99-8460-456b5c87d63f --> 7
a62750dd-ac20-4f3f-9db2-9367e7b42edb --> a
fb141873-96a2-4d89-abe1-bb221a71431c --> f
2731f679-7869-4814-a9e0-3925387e3fba --> 2
17030217-af4e-469f-9547-8ff79d8291da --> 1
0cd5d09a-9bab-43df-84f2-455749bd099f --> 0
2ac6eeeb-d72b-4571-bb19-abdadb88f1c7 --> 2
5346aebc-ff59-4b59-9651-2e90077260c6 --> 5
1614c298-f7a3-494d-8cf9-e0e5b5337b28 --> 1
e4e26268-ece6-4780-9082-9d04b116bc4a --> e
0230463b-153e-40cb-a4b9-20eff12b1cb3 --> 0
924dcecb-e90e-4279-a4b8-d0be63d07a37 --> 9
dec42983-62ef-4ea4-8d88-216d6c4d7e90 --> d
db36c89f-3908-4796-a932-e8668c325edf --> d
0eb10540-6436-404e-9cb1-990eed5ae893 --> 0
01524219-ecae-4db1-842c-be47275ecab4 --> 0
a72c181e-8e81-4bb0-bb7d-02302f1231d0 --> a
315eb1d5-52b4-4f45-a31b-627dd5c54426 --> 3
6c365089-7f60-4425-a397-b8bd007c99ed --> 6
6bc09737-528f-44e9-a56f-df84067def2c --> 6
35eeeac3-6a

d8d128b7-40fb-47ba-a7ca-0dee9769966a --> d
33ebaae5-785c-4839-975a-0787a614576f --> 3
d3bac156-46a5-4b22-8f12-6439c5bf00fb --> d
1774e741-2598-4fd0-b9c0-df35c4840ec3 --> 1
af2f9c45-8c91-49a1-aae6-b4888e1b2139 --> a
6b2a173e-b7de-400b-a49f-a186e1e74227 --> 6
1b5c67d8-c5d0-49ed-84f5-6b68bcb75ba9 --> 1
27d34a16-c763-48b6-9c80-95131d1f59f7 --> 2
ed335441-7211-4bec-957c-89d06b086576 --> e
36a6bb65-681a-4325-8a55-9314fbf225ee --> 3
eb7e8bb6-6c3b-44d2-9bbf-20e8281f282c --> e
aac796b1-a5d7-465d-9425-3af7fe2e0488 --> a
af80f836-80ec-4379-bb7f-cb49cbfd3741 --> a
a5d35e81-8e7f-438a-87a5-09f9cab69bc6 --> a
071f4eec-1287-436f-8e96-677b776ca2fd --> 0
e66c9375-dbd0-4b07-87a7-bf0801190bfd --> e
6262d29e-9fce-4c27-af19-acb0ba453099 --> 6
e4a911b6-eca0-4a81-bafd-b4378d394dfa --> e
8d6f04b4-d65d-4f6c-afa6-785cbeccfa7b --> 8
0013fe62-5bc6-4046-bc33-d01ce370cd86 --> 0
579eaf59-6503-4336-9b9e-a6cba9011156 --> 5
c032e2f2-0b75-438f-8168-c10579f4fc10 --> c
6b4cbc10-1b5d-4988-9357-931d227405dd --> 6
94c0d6aa-1d

...

c25154b1-8684-473c-bfa2-8a6e4a6a2738 --> c
bebf40bd-6086-42ac-9f04-b707d6f8947d --> b
08b7520a-8efc-4e97-8346-fac8e3341854 --> 0
06dc1db9-d517-4dce-ac55-a4da92a1ebb1 --> 0
9a871ae6-a494-44af-bfb1-05365987e2d0 --> 9
21b9acc4-1412-4334-b464-787733f87659 --> 2
3a1767a0-b3f9-458a-bb0b-f0f29bec1dd7 --> 3
3d5fefcb-b504-42d3-b155-83f3f16f8038 --> 3
1354c0c6-8ed2-42e0-87b2-d37c666687e1 --> 1
b0923ae5-de1b-4cb9-9412-fa03daa89a7e --> b
082d7e66-f609-41ea-9d5e-1c9f4592c92e --> 0
6da1c440-07fe-4ba6-8122-18557fcdde87 --> 6
22ac692f-4c52-4bbd-90a6-ca38a7f34663 --> 2
1ec8dc8e-ffce-450f-9ed5-7d406c17ac4c --> 1
17e655bc-7acc-4b7b-8da8-311c4ad2b479 --> 1
7019088b-c408-4f95-baaf-6a494cf29635 --> 7
4b85c4fc-04ff-4205-8a81-579714381e86 --> 4
5b403cf5-6193-4231-89f1-f774130e5d8f --> 5
3ecf5d8f-ffb1-4e55-8d24-ae1d9fb8710c --> 3
62b2ffb9-dc1f-4136-99f8-032913cc53b4 --> 6
ebe4dc48-0875-42df-b63d-57b05d448042 --> e
a47bec7d-2545-417e-8ceb-edcdea802e1c --> a
b35994f0-131b-436e-ac8f-5bb089347929 --> b
4a2e8608-d3

162866ea-bb44-4962-ae7a-d43c0c35963e --> 1
3237258a-170d-4643-a368-7e670f2f1e18 --> 3
3bf98d20-9c80-4ef7-bcb1-88d740700104 --> 3
8324a187-1386-4aee-b820-fafbee850eb7 --> 8
58b68331-0f16-41de-90de-16f02c4dfd53 --> 5
716dcd02-b459-4041-b62d-caab1cddf26e --> 7
ccc6ac46-a94a-4f75-bcae-625ee5ce8362 --> c
ea8ab972-a0b0-4d48-8ab9-92c222e24bbe --> e
7ee2c2e3-ad2f-4bcc-8266-bcfa62daedd5 --> 7
b44ba7b1-7e6d-4b53-85f7-9b0d58ae3e38 --> b
3ab53904-d741-4f6b-a75a-6db497cca3bd --> 3
1a71ec76-8f83-41cb-81cf-7ed0197a8a00 --> 1
bfddcd06-820b-492f-bfb9-4c795da8f5bb --> b
2ca78eee-48ac-41f8-9367-d2caba5fcbc8 --> 2
b6a42ce0-87e2-4a90-b402-2bc8cd42974a --> b
ce7ac3d6-6039-4230-97dd-a48bf214fb9c --> c
0c1a4d9f-6faf-436a-9906-d120f895c537 --> 0
4e438e91-bf2f-4125-8c39-56871a54ca9a --> 4
5abf9c41-2d6e-4c33-bef5-ff80eab565c8 --> 5
aa22a5c5-c9c7-43b3-ad8a-d2d719d0f464 --> a
c67aabbd-a152-4f12-acb1-c2137de84696 --> c
12815800-83c6-422d-b353-304d1bdd6367 --> 1
cb0c0440-dcf0-492e-bdcf-e197d2e0cb18 --> c
5bb97c56-95

bee58aa4-0c39-449b-8762-4dc45ef91d0d --> b
456e8d9b-8d7f-46a1-bddc-f137fa9266c7 --> 4
d2a258e7-eeb1-4199-af80-556c53b6c7bf --> d
6f8dad76-1fad-41b6-8a07-a277c94a347b --> 6
d47ef689-ab46-4ccd-b86a-d14afecd2dcd --> d
2fbf18c0-d612-4d66-b649-04af715165a1 --> 2
3d8359ef-c3d4-4f37-998b-91f012e6c02c --> 3
83fd28eb-a2ef-4c7b-8af4-07d534be4f36 --> 8
b396a894-8606-4ba5-8d98-24d717549c22 --> b
bc6f30c2-88fc-4b5f-9f6c-517ad8b1f2c8 --> b
ace3e074-3f55-41c7-9c0f-384d46dd0b58 --> a
15e17f94-73e0-41f2-b669-c48212fe9095 --> 1
6fa46102-12a0-4c00-ba48-aa89ea84a212 --> 6
c4b7ef8f-ad0f-418e-81fb-fd391a09f4fe --> c
4f08c78b-e1d5-4d7e-a73a-3016ba4e8223 --> 4
25565b3a-3038-441b-a279-bfd258409f55 --> 2
1849bbe7-071e-49e0-ac4e-6ae69f1b705c --> 1
63ffcf33-803d-4b9f-8337-76cca5edb3b9 --> 6
7950d059-418f-432f-aab9-316aa07d95ae --> 7
dac4401c-0852-4c78-a3ef-74869dc5f200 --> d
fc696cac-c300-4836-91c5-1164e90a35db --> f
09bdad67-47ac-4cce-9701-1c714552b11f --> 0
8532019c-d3c5-471f-ad45-246643835314 --> 8
c564bd44-d5

7b0879d2-52a0-4c21-9885-197aedaf6eae --> 7
08ac6a10-a3fa-4bd3-b68f-c5f3f6d2fc99 --> 0
a8fa8861-9c69-4547-95dd-05fe9726bb25 --> a
e18c7f1e-a3db-4820-ab7b-dd80b0c8ab74 --> e
52b0e803-b722-4f99-a962-1fd85b6c20f5 --> 5
e9361034-863e-4b9f-a043-569d35d5c01e --> e
92395833-4b62-4970-b7ca-e58916be3242 --> 9
e43aedb5-5f01-4df9-bab9-5882b361623e --> e
8b0e76e5-53e2-4e8b-8a21-c63f9642bf09 --> 8
355f5c59-a653-4dd9-baf7-935dbf547d17 --> 3
1111411d-45a5-41fe-95ab-1dd6fa7f9f77 --> 1
9979e2b6-12ad-4bf6-916b-9efb02740076 --> 9
5517cd8e-e72b-436b-8d9e-b54821e29053 --> 5
6b1ad02b-0fbf-40ae-af9d-ea081ae170ef --> 6
9f59a027-2554-423b-a8b7-a2cbd82c5827 --> 9
2b541a7f-d9c8-4adb-92d9-8fae955809b1 --> 2
03314a81-e02e-42f7-b874-9fe361de0954 --> 0
52600777-c3c0-4ccc-9430-92448708c12e --> 5
600740d6-4ccf-4325-8ad6-47575c3dd9fa --> 6
aac98513-0f9a-4d11-828a-b7be63338c69 --> a
7c57b791-cb7d-4095-a850-ef7791565919 --> 7
7bdcf9e9-55aa-4e3a-b5a0-e6ba51446140 --> 7
0556712b-c840-46b0-84be-1430dc304330 --> 0
3d5abf7c-f2

'/home/marrakchi/TFM/TFM_env/Datasets/ExKaldiASRDatasetFormat/data/test/spk2utt'

In [57]:
# Prepare wav.scp file
wavScp = exkaldi.ListTable(name="wavScp")
for name in wav_list:
    wavFilePath = os.path.join(path_dataset,'wav/',name)
    wavScp[name[:-4]] = wavFilePath
wavScp.sort().save(os.path.join(path_dataset,"wav.scp") )

# Remove all rows that contain wav files with no transcriptions
rem = []
for i,item in enumerate (wavScp):
    #if i==0:
    #    print(item)
    if item not in trans:
        rem.append(item)

#print(rem) # uttIDs that have no transcription
new_keys = [x[:-4] for x in wav_list if x[:-4] not in rem]
#print(len(new_keys))
new_wavScp = wavScp.subset(keys=new_keys)
new_wavScp.save(os.path.join(path_dataset,"wav.scp") )


'\n# Remove all rows that contain wav files with no transcriptions\nrem = []\nfor i,item in enumerate (wavScp):\n    #if i==0:\n    #    print(item)\n    if item not in trans:\n        rem.append(item)\n\n#print(rem) # uttIDs that have no transcription\nnew_keys = [x[:-4] for x in wav_list if x[:-4] not in rem]\n#print(len(new_keys))\nnew_wavScp = wavScp.subset(keys=new_keys)\nnew_wavScp.save(os.path.join(path_dataset,"wav.scp") )\n'

In [180]:
# Prepare transcription file
transcription = exkaldi.Transcription(name="trans")

# Read dataset transcriptions
X = pd.read_csv(CSV_FILE_PATH_1, sep="|", header=None, names=["path","label"],usecols=[0,1])
X2 = pd.read_csv(CSV_FILE_PATH_2, sep=",", usecols=[0, 2])
X2.columns=['path','label']

# Mix both datasets into one
data = pd.concat([X, X2], ignore_index=True)

# Remove all rows with Utterance value missing
data.dropna(subset = ['label'], inplace=True)
# Drop all containing digits:
data = data.drop(data[data.label.str.contains(r'\d+')].index)
# Change path with uttID (Name of the wav file instead of path)
data.columns=['uttID','transcription']
#data['uttID']= data['uttID'].str.slice(start=data['uttID'].str.rfind('/'),stop=data['uttID'].str.rfind('.'))
data[['path','uttID']] = data.uttID.str.split("/",expand=True)
data[['uttID','suffix']] = data.uttID.str.split(".",expand=True)

# Label to lower case
data['transcription'] = data['transcription'].str.lower()
# Remove punctuations:
data['transcription'] = data['transcription'].str.replace('[{}]'.format(string.punctuation), '')
# Convert to plain text. Remove accents and any other symbols like ¨, æ, etc. 
data['transcription'] = data['transcription'].str.normalize('NFKD').str.encode('ascii', errors='ignore').str.decode('utf-8')

#Convert to dataframe format and drop extra columns
df = pd.DataFrame(data)
df = df.drop(columns=['path','suffix'])
df = df.reset_index(drop=True) # Refrech indexes

for num,row in enumerate (df.uttID):
    transcription[row] = df.transcription[num]
transcription.sort().save( os.path.join(path_dataset, "text") )

#Display
display(HTML(df[331:337].to_html()))


In [68]:
## Separate train and test transcription files
# Load transcription file
trans = exkaldi.load_transcription(os.path.join(path_dataset,"text"))
print(len(trans))
# Shuffle to get a randpom split
trans2 = trans.shuffle()
# 80% of data in train (99023)
trainTrans = trans2.subset(nHead=int(0.8*len(trans)))
print(len(trainTrans))
# 20% of data in test (24756)
testTrans = trans2.subset(nTail=len(trans)-int(0.8*len(trans)))
print(len(testTrans))
# Save transcription objects into files
trainTrans.save( os.path.join(path_dataset,'data/train', "text") )
testTrans.save( os.path.join(path_dataset,'data/test', "text") )


123779
99023
24756


In [66]:
## Separate testTrans into dev and test
# ... (80% train) | 18% val | 2% test
# Load transcriptions
trans = exkaldi.load_transcription(os.path.join(path_dataset,"text"))
trainTrans = exkaldi.load_transcription(os.path.join(path_dataset,'data/train',"text"))
testTrans = exkaldi.load_transcription(os.path.join(path_dataset,'data/test',"text"))

valTrans = testTrans.subset(nHead=round(0.9*len(testTrans)))
print(len(valTrans))
testTrans = testTrans.subset(nTail=len(testTrans)-round(0.9*len(testTrans)))
print(len(testTrans))
# Save transcription objects into files
valTrans.save( os.path.join(path_dataset,'data/val', "text") )
testTrans.save( os.path.join(path_dataset,'data/test', "text") )

#train --> 99023
#val --> 22280
#test --> 2476

# Devide wavScp into train, val, test (as with transcriptions)
wavScp = exkaldi.load_list_table(os.path.join(path_dataset,"wav.scp") )
train_keys = []
val_keys = []
test_keys = []

for i,item in enumerate(trainTrans):
    if i==0:
        print(item)
    train_keys.append(item)

for item in valTrans:
    val_keys.append(item)
    
for item in testTrans:
    test_keys.append(item)

wavScp_train = wavScp.subset(keys= train_keys)
wavScp_val = wavScp.subset(keys= val_keys)
wavScp_test = wavScp.subset(keys= test_keys)

print(len(wavScp_train))
print(len(wavScp_val))
print(len(wavScp_test))

# Save transcription objects into files
wavScp_train.save( os.path.join(path_dataset,'data/train', "wav.scp") )
wavScp_val.save( os.path.join(path_dataset,'data/val', "wav.scp") )
wavScp_test.save( os.path.join(path_dataset,'data/test', "wav.scp") )

In [61]:
# Creating ListTable that convert words to phones through txt file
import unicodedata

# Read txt file as a dict
word_phone = {}
word_phone['<UNK>'] = '<algo>'
with open(mi_path) as f:
    for line in f:
        bu[:-2] = line.split(maxsplit=1)
        word_phone[unicodedata.normalize('NFKD', bu[0]).encode('ascii','ignore').decode('utf-8')] = bu[1][:-1]
        
# Save dict as ListTable
word2phone = exkaldi.load_list_table(word_phone)
word2phone.save(path_dataset+'word2phone.map')


'/home/marrakchi/TFM/TFM_env/Datasets/ExKaldiASRDatasetFormat/word2phone.map'

# Audio Sample
* First hear an audio from the spanish-single-speaker-speech-dataset and plot.
* Second hear an audio from the 120h-spanish-speech and plot.

In [5]:
samp_path = path_dataset+'wav/batalla_arapiles_0000.wav'
ipd.display.Audio(filename=samp_path)

In [6]:
# Compute MFCC
feat = exkaldi.compute_mfcc(samp_path, name="mfcc")
print(feat)
# Compute spectrogram
# default args: frameWidth=25, frameShift=10, windowType='povey'
feat2 = exkaldi.compute_spectrogram(samp_path, rate=22050, name="spectrogram")
print(feat2)
# Feature dimensions
print(feat.dim)
print(feat2.dim)
# Feature utterances
print(feat.utts)
print(feat2.utts)

13
513
['batalla_arapiles_0000']
['batalla_arapiles_0000']


# Dictionary (lexicon) and language model

In [73]:
# Prepare lexicon
lexiconFile = os.path.join(path_dataset, "pronunciation.txt")

silWords={"<SIL>":"<SIL>",  # silence and its' pronunciation
          "<SPN>":"<SPN>"}  # spoken noise and its' pronunciation
unkSymbol={"<UNK>":"<SPN>"}  # unknown symbol and its' pronunciation
optionalSilPhone = "<SIL>"  # optional silence

lexicons = exkaldi.decode.graph.lexicon_bank(lexiconFile,
                                             silWords,
                                             unkSymbol, 
                                             optionalSilPhone, 
                                             positionDependent = False,
                                             shareSilPdf = False )

print(lexicons)
print('\n Generated lexicons =>')
print(lexicons.view) #  show all names of generated lexicons.

# Save this lexicon bank for future use.
lexicons.save(os.path.join(path_dataset, "dict", "lexicons.lex"))

# Generate the Lexicon fst
exkaldi.decode.graph.make_L(lexicons, 
                            outFile=os.path.join(path_dataset,"dict","L.fst"),
                            useDisambigLexicon=False)

# Generate the disambig Lexicon fst
exkaldi.decode.graph.make_L(lexicons, 
                        outFile=os.path.join(path_dataset,"dict","L_disambig.fst"), 
                        useDisambigLexicon=True)

# Make GMM-HMM topological structure for GMM-HMM 
exkaldi.hmm.make_topology(
                        lexicons,
                        outFile=os.path.join(path_dataset,"dict","topo"),
                        numNonsilStates=3,
                        numSilStates=5,)



 Generated lexicons =>
['lexiconp', 'disambig', 'lexiconp_disambig', 'silence_phones', 'optional_silence', 'nonsilence_phones', 'phone_map', 'silence_phone_map', 'nonsilence_phone_map', 'extra_questions', 'silence', 'nonsilence', 'context_indep', 'wdisambig', 'wdisambig_phones', 'wdisambig_words', 'align_lexicon', 'oov', 'sets', 'roots', 'phones', 'words']


'/home/marrakchi/TFM/Datasets/ExKaldiASRDatasetFormat/dict/L_disambig.fst'

In [5]:
# Load lexicon
lexicons = exkaldi.load_lex(os.path.join(path_dataset, "dict", "lexicons.lex"))
print(lexicons)
# Load transcriptions
trans = exkaldi.load_transcription(os.path.join(path_dataset,"text"))
trainTrans = exkaldi.load_transcription(os.path.join(path_dataset,'data/train',"text"))
valTrans = exkaldi.load_transcription(os.path.join(path_dataset,'data/val',"text"))
testTrans = exkaldi.load_transcription(os.path.join(path_dataset,'data/test',"text"))
# Load wavScp
wavScp = exkaldi.load_list_table(os.path.join(path_dataset,"wav.scp") )
wavScp_train = exkaldi.load_list_table(os.path.join(path_dataset,'data/train',"wav.scp") )
wavScp_val = exkaldi.load_list_table(os.path.join(path_dataset,'data/val',"wav.scp") )
wavScp_test = exkaldi.load_list_table(os.path.join(path_dataset,'data/test',"wav.scp") )

In [10]:
# Load lexicon
lexicons = exkaldi.load_lex(os.path.join(path_dataset, "dict", "lexicons.lex"))


{'<SPN>': ('<SPN>',),
 '<SIL>': ('<SIL>',),
 'a': ('a',),
 'b': ('b',),
 'd': ('d',),
 'f': ('f',),
 'g': ('g',),
 'i': ('i',),
 'j': ('j',),
 'k': ('k',),
 'l': ('l',),
 'm': ('m',),
 'n': ('n',),
 'o': ('o',),
 'p': ('p',),
 'r': ('r',),
 's': ('s',),
 't': ('t',),
 'u': ('u',),
 'w': ('w',),
 'x': ('x',),
 'ɛ': ('ɛ',),
 'ɲ': ('ɲ',),
 'ɾ': ('ɾ',),
 'ʎ': ('ʎ',),
 'ʧ': ('ʧ',)}